<a href="https://colab.research.google.com/github/w-okada/voice-changer/blob/dev/VoiceChangerDemo_Simple.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

MMVCプレイヤー（超簡単版）
---

このノートはColab上でMMVCのボイチェンを行うノートです。

正式版はローカルPCのDocker上で動かすアプリケーションです。

正式版は、多くの場合より少ないタイムラグで滑らかに音声を変換できます。

詳細な使用方法はこちらの[リポジトリ](https://github.com/w-okada/voice-changer)からご確認ください。


# GPUを確認
GPUを用いたほうが高速に処理が行えます。

下記のコマンドでGPUが確認できない場合は、上のメニューから

「ランタイム」→「ランタイムの変更」→「ハードウェア アクセラレータ」

でGPUを選択してください。

In [1]:
# (1) GPUの確認
!nvidia-smi

Fri Jan 13 22:07:27 2023       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 460.32.03    Driver Version: 460.32.03    CUDA Version: 11.2     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla T4            Off  | 00000000:00:04.0 Off |                    0 |
| N/A   40C    P8     9W /  70W |      0MiB / 15109MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

# リポジトリのクローン
リポジトリをクローンします

In [2]:
# (2) リポジトリのクローン
!git clone --depth 1 https://github.com/w-okada/voice-changer.git  -b v.1.3.4
%cd voice-changer/server
!git clone https://github.com/isletennos/MMVC_Client.git
!cd MMVC_Client && git checkout 04f3fec4fd82dea6657026ec4e1cd80fb29a415c && cd -


Cloning into 'voice-changer'...
remote: Enumerating objects: 144, done.
remote: Counting objects: 100% (144/144), done.
remote: Compressing objects: 100% (129/129), done.
remote: Total 144 (delta 20), reused 62 (delta 5), pack-reused 0
Receiving objects: 100% (144/144), 1.52 MiB | 4.11 MiB/s, done.
Resolving deltas: 100% (20/20), done.
/content/voice-changer/server
Cloning into 'MMVC_Client'...
remote: Enumerating objects: 594, done.
remote: Counting objects: 100% (320/320), done.
remote: Compressing objects: 100% (114/114), done.
remote: Total 594 (delta 229), reused 261 (delta 203), pack-reused 274
Receiving objects: 100% (594/594), 738.87 KiB | 23.83 MiB/s, done.
Resolving deltas: 100% (351/351), done.
Note: checking out '04f3fec4fd82dea6657026ec4e1cd80fb29a415c'.

You are in 'detached HEAD' state. You can look around, make experimental
changes and commit them, and you can discard any commits you make in this
state without impacting any branches by performing another checkout.

If y

# モジュールのインストール

必要なモジュールをインストールします。

In [3]:
# (3) 設定ファイルの確認
!apt-get install -y libsndfile1-dev &> /dev/null
!pip install fastapi &> /dev/null
!pip install pyOpenSSL &> /dev/null
!pip install python-multipart &> /dev/null
!pip install python-socketio &> /dev/null
!pip install uvicorn &> /dev/null
!pip install websockets &> /dev/null
!pip install onnxruntime-gpu &> /dev/null


# サーバの起動

サーバを起動します。(4-1)

サーバの起動状況を確認します。(4-2) 

このセルは繰り返し実行することになるのでCtrl+Retでセルを実行してください。

下記のようなテキストが表示されたら起動完了です。

**`DEBUG:asyncio:Using selector: EpollSelector`**

```
    Phase name:__main__
    PHASE3:__main__
    PHASE1:__main__
Start MMVC SocketIO Server
    CONFIG:None, MODEL:None ONNX_MODEL:None
```



In [4]:
# (4-1) サーバの起動
import random
PORT = 10000 + random.randint(1, 9999)
LOG_FILE = f"LOG_FILE_{PORT}"

get_ipython().system_raw(f'python3 MMVCServerSIO.py -t MMVC -p {PORT} --colab True >{LOG_FILE} 2>&1 &')
#print(f"PORT:{PORT}, LOG_FILE:{LOG_FILE}")

In [5]:
# (4-2) サーバの起動確認
!sleep 30
!tail -20 {LOG_FILE}

    Phase name:__main__
    PHASE3:__main__
    PHASE1:__main__
Start MMVC SocketIO Server
    CONFIG:None, MODEL:None ONNX_MODEL:None


# プロキシを起動
ウェブサーバへのアクセスをするためのプロキシを起動します。

表示されたURLをクリックして開くと別タブでアプリが開きます。

Colabなので、ロードにある程度時間がかかります(30秒くらい)。

In [6]:
# (5) プロキシを起動
from google.colab.output import eval_js
proxy = eval_js( "google.colab.kernel.proxyPort(" + str(PORT) + ")" )
print(f"{proxy}front/?colab=true")

https://v8lm07nxaxe-496ff2e9c6d22116-10766-colab.googleusercontent.com/front/?colab=true
